## Introduction 

This notebook shows how to import data from a csv file. There are several ways to achieve this. 

Here, we combine two approaches:
- 1) import the data as a data frame with `Deedle`
- 2) instead of staying in `Deedle` for the whole analysis, we leave the data frame early and model our rows as a collection of Record Types.

## NuGet
NuGet is the package manager for .NET. #r directives can be copied to `.fsx` scripts or polyglot notebooks to get access to libraries.

Packages suffixed with `.Interactive` are usually special packages that 

In [11]:
// nuget references
#r "nuget: Deedle, 3.0.0"
#r "nuget: Deedle.Interactive, 3.0.0"

// the specified library namespaces are opened 
open Deedle

Installed Packages Deedle, 3.0.0 Deedle.Interactive, 3.0.0

## Shape of the data

Before we can model our data, let's have a look at it. You could do this by opening the file in any text editor, but wen can also do this without leaving our programming environment.

Let's parse the CSV file with `Deedle`, a data frame library.

In [12]:
let df = Frame.ReadCsv("../../data/coffeedata.txt", separators="\t")

df

DateTime Name Gender Product Price Department Category Amount (string) (string) (string) (string) (Decimal) (string) (string) (int) 
 0 -> 23/08/2018 10:37:40 Archie Nelson m Coffee_2022_2_3 0.3 Toon Squad Coffee 1 1 -> 23/08/2018 10:37:46 Archie Nelson m Coffee_2022_2_3 0.3 Toon Squad Coffee 1 2 -> 23/08/2018 10:47:57 Timo M. m Coffee_2022_2_3 0.3 Recruitables Coffee 1 3 -> 23/08/2018 13:57:54 Douglas Powell m Coffee_2022_2_3 0.3 Recruitables Coffee 1 4 -> 23/08/2018 14:00:52 Timo M. m Coffee_2022_2_3 0.3 Recruitables Coffee 1 : ... ... ... ... ... ... ... ... 38107 -> 19/09/2023 15:02:47 Benedikt V. m Coffee 0.25 Recruitables Coffee 1 38108 -> 19/09/2023 15:53:12 Kevin S. m Coffee 0.25 Recruitables Coffee 1 38109 -> 19/09/2023 16:13:41 Benedikt V. m Spezi 0.5l 0.8 Recruitables Beverage 1 38110 -> 19/09/2023 16:34:09 Zachary Mitchell m Augustiner Lager Hell 1.3 Breakroom Bandits Beer 1 38111 -> 19/09/2023 17:17:44 Zachary Mitchell m Augustiner Lager Hell 1.3 Breakroom Bandits Beer 1 
 
 38112 rows x 8 columns 0 missing values

## Type modelling

By inspecting the data frame, we can get an idea of the shape of the data. Deedle also infers column types, which becomes quite handy when we want to model our data.

Looking at the frame's column headers we see the following:
| Header | Type |
| --- | --- |
| `DateTime` | `string` |
| `Name` | `string` |
| `Gender` | `string` |
| `Product` | `string` |
| `Price` | `Decimal` |
| `Department` | `string` |
| `Category` | `string` |
| `Amount` | `int` |



However, let us additionally model `Category` as a union case. We could theoretically do that for all data that seems to be categorical, but we will focus only on `Category` here. Feel free to do it though!

Let's take a look at the distinct values in the `Category` column to get our Union Cases:

In [13]:
df
|> Frame.getCol "Category"
|> Series.values
|> Seq.cast<string>
|> Seq.distinct
|> Array.ofSeq

[ Coffee, Beer, Beverage, Deposit, TestStuff, Debit, Food, Milk, Hardware, Misc ]

In [14]:
type Category =
    | Coffee
    | Beer
    | Beverage
    | Deposit
    | TestStuff
    | Debit
    | Food
    | Milk
    | Hardware
    | Misc
    with 
        /// takes a string that describes the category and returns the corresponding category type
        static member fromString (s: string) =
            match s with
            | "Coffee" -> Coffee
            | "Beer" -> Beer
            | "Beverage" -> Beverage
            | "Deposit" -> Deposit
            | "TestStuff" -> TestStuff
            | "Debit" -> Debit
            | "Food" -> Food
            | "Milk" -> Milk
            | "Hardware" -> Hardware
            | "Misc" -> Misc
            | _ -> failwith "Unknown category"


Now that we have a good idea about our data, let's transform the rows into records of type `Order`.

We recommend to change the `Decimal` row into a float, as we do not need the additional precision provided by `Decimal`.


In [15]:
type Order = {
    DateTime    : System.DateTime
    Name        : string
    Gender      : string
    Product     : string
    Price       : float
    Department  : string
    Category    : Category
    Amount      : int
    } with
        /// takes data row entities as input and creates a Order record type
        static member create time (name: string) gender product price department category amount = {
            DateTime  = time
            Name      = name
            Gender    = gender
            Product   = product
            Price     = price
            Department= department
            Category  = category
            Amount    = amount
            }

By mapping throuh the dataframe rows, we can transform each row into a record of type `Order`.

In [16]:
let orders = 
    df
    |> Frame.mapRows (fun key row ->
        {
            DateTime = System.DateTime.ParseExact((row.GetAs<string>("DateTime")),"dd/MM/yyyy HH:mm:ss",null)
            Name = row.GetAs<string>("Name")
            Gender = row.GetAs<string>("Gender")
            Product = row.GetAs<string>("Product")
            Price = row.GetAs<float>("Price")
            Department = row.GetAs<string>("Department")
            Category = row.GetAs<string>("Category") |> Category.fromString
            Amount = row.GetAs<int>("Amount")
        }
    )
    |> Series.values
    |> Array.ofSeq
    |> Array.sortBy (fun x -> x.DateTime)

orders
|> DisplayExtensions.DisplayTable

DateTime Name Gender Product Price Department Category Amount 2018-08-23 07:31:30Z Justin Bennett m Bluna Orange 0.2 l 0.8 Employees of the Moment Beverage 1 2018-08-23 08:18:00Z Timo M. m Coffee_2022_2_3 0.3 Recruitables Coffee 1 2018-08-23 08:54:36Z Nicholas Thomas m Coffee_2022_2_3 0.3 Recruitables Coffee 1 2018-08-23 09:03:51Z Archie Nelson m Coffee_2022_2_3 0.3 Toon Squad Coffee 1 2018-08-23 09:19:47Z Benedikt V. m Coffee_2022_2_3 0.3 Recruitables Coffee 1 2018-08-23 09:27:45Z Timo M. m Coffee_2022_2_3 0.3 Recruitables Coffee 1 2018-08-23 09:45:57Z Archie Nelson m Coffee_2022_2_3 0.3 Toon Squad Coffee 1 2018-08-23 09:59:55Z Philip Reilly m Coffee_2022_2_3 0.3 Employees of the Moment Coffee 1 2018-08-23 10:02:30Z Hugo Green m Coffee_2022_2_3 0.3 Breakroom Bandits Coffee 1 2018-08-23 10:20:12Z Douglas Powell m Coffee_2022_2_3 0.3 Recruitables Coffee 1 2018-08-23 10:27:49Z Muhammed Sullivan m Coffee_2022_2_3 0.3 Recruitables Coffee 1 2018-08-23 10:37:40Z Archie Nelson m Coffee_2022_2_3 0.3 Toon Squad Coffee 1 2018-08-23 10:37:46Z Archie Nelson m Coffee_2022_2_3 0.3 Toon Squad Coffee 1 2018-08-23 10:47:57Z Timo M. m Coffee_2022_2_3 0.3 Recruitables Coffee 1 2018-08-23 11:13:36Z Scott Woods m Coffee_2022_2_3 0.3 Recruitables Coffee 1 2018-08-23 12:42:26Z Douglas Powell m Coffee_2022_2_3 0.3 Recruitables Coffee 1 2018-08-23 12:42:40Z Nicholas Thomas m Coffee_2022_2_3 0.3 Recruitables Coffee 1 2018-08-23 12:42:46Z Patrick Holmes m Coffee_2022_2_3 0.3 Recruitables Coffee 1 2018-08-23 12:43:00Z Muhammed Sullivan m Coffee_2022_2_3 0.3 Recruitables Coffee 1 2018-08-23 13:24:47Z Benedikt V. m Coffee_2022_2_3 0.3 Recruitables Coffee 1 (38092 more)

We successfully modeled and imported the data set. Now we can take a dive into the data and try to use data science to reveal interesting properties or surpising discoveries.

For a first glance lets check which time frame the data covers:

In [17]:
let firstLog = Array.minBy (fun x -> x.DateTime) orders
let lastLog  = Array.maxBy (fun x -> x.DateTime) orders

firstLog,lastLog

({ DateTime = 8/23/2018 7:31:30 AM\n Name = "Justin Bennett"\n Gender = "m"\n Product = "Bluna Orange 0.2 l"\n Price = 0.8\n Department = "Employees of the Moment"\n Category = Beverage\n Amount = 1 }, { DateTime = 9/19/2023 5:17:44 PM\n Name = "Zachary Mitchell"\n Gender = "m"\n Product =... Item1 { DateTime = 8/23/2018 7:31:30 AM\n Name = "Justin Bennett"\n Gender = "m"\n Product = "Bluna Orange 0.2 l"\n Price = 0.8\n Department = "Employees of the Moment"\n Category = Beverage\n Amount = 1 } DateTime 2018-08-23 07:31:30Z Name Justin Bennett Gender m Product Bluna Orange 0.2 l Price 0.8 Department Employees of the Moment Category Beverage Amount 1 Item2 { DateTime = 9/19/2023 5:17:44 PM\n Name = "Zachary Mitchell"\n Gender = "m"\n Product = "Augustiner Lager Hell"\n Price = 1.3\n Department = "Breakroom Bandits"\n Category = Beer\n Amount = 1 } DateTime 2023-09-19 17:17:44Z Name Zachary Mitchell Gender m Product Augustiner Lager Hell Price 1.3 Department Breakroom Bandits Category Beer Amount 1

How many Persons are involved and how many products are available?

In [18]:
let personsCount =
    orders
    |> Array.distinctBy (fun x -> x.Name)
    |> Array.length

let productCount =
    orders
    |> Array.distinctBy (fun x -> x.Product)
    |> Array.length

$"Persons: {personsCount}\nProducts: {productCount}"

Persons: 155
Products: 212

How many coffees, beers and beverages were ordered?

In [19]:
let coffeelogs   = orders |> Array.filter (fun x -> x.Category = Coffee)   |> Array.length
let beerlogs     = orders |> Array.filter (fun x -> x.Category = Beer)     |> Array.length
let beveragelogs = orders |> Array.filter (fun x -> x.Category = Beverage) |> Array.length

$"Coffee: {coffeelogs}\nBeer: {beerlogs}\nBeverage: {beveragelogs}"

Coffee: 21484
Beer: 4647
Beverage: 10481

What properties do you want to check next?

Some inspiration:
- total revenue
- revenue per product
- revenue per category